
## 주요 구성 요소

1. **PDF 처리 및 텍스트 청킹 (Chunking)**: PDF 문서를 다루고 적절한 크기의 텍스트 조각으로 분할.
2. **질문 증강**: `OpenAI 언어 모델을 사용하여 문서 및 텍스트 조각 레벨에서 관련 질문 생성.`
3. **벡터 스토어 생성**: OpenAI 임베딩 모델을 사용해 문서 임베딩 계산 후 FAISS 벡터 스토어 생성.
4. **검색 및 답변 생성**: FAISS에서 가장 관련성 높은 문서를 검색하고, 검색된 문서를 기반으로 답변 생성.

## 방법론

### 문서 전처리

1. LangChain의 `PyPDFLoader`를 사용해 PDF를 문자열로 변환.
2. 텍스트를 문맥 유지를 위해 중첩된 텍스트 문서(`text_document`)로 나눈 후, 검색과 의미 검색을 위해 각 문서를 다시 중첩된 텍스트 조각(`text_fragment`)으로 나눕니다.

### 문서 증강

1. OpenAI 언어 모델을 사용하여 문서나 텍스트 조각 레벨에서 관련 질문을 생성.
2. `QUESTIONS_PER_DOCUMENT` 상수를 통해 문서당 생성할 질문 수를 설정.

### 벡터 스토어 생성

1. `OpenAIEmbeddings` 클래스를 사용해 문서 임베딩을 계산.
2. 계산된 임베딩으로 FAISS 벡터 스토어 생성.

### 검색 및 생성

1. 주어진 쿼리에 따라 FAISS 스토어에서 가장 관련성 높은 문서를 검색.
2. 검색된 문서를 기반으로 OpenAI 언어 모델을 사용해 답변 생성.

## 이 접근법의 장점

1. **향상된 검색 과정**: 주어진 쿼리에 가장 관련성 높은 FAISS 문서를 찾을 확률이 증가.
2. **유연한 문맥 조정**: 텍스트 문서와 조각의 문맥 창 크기를 쉽게 조정 가능.
3. **고품질 언어 이해**: 질문 생성과 답변 생성에 OpenAI의 강력한 언어 모델을 활용.

## 구현 세부 사항

- `OpenAIEmbeddingsWrapper` 클래스는 일관된 임베딩 생성 인터페이스를 제공합니다.
- `generate_questions` 함수는 OpenAI의 채팅 모델을 사용하여 텍스트에서 관련 질문을 생성합니다.
- `process_documents` 함수는 문서 분할, 질문 생성 및 벡터 스토어 생성의 핵심 로직을 담당합니다.
- 메인 실행에서는 PDF를 로드하고, 내용을 처리하며, 샘플 쿼리를 수행합니다.

## 결론

이 기술은 벡터 기반 문서 검색 시스템에서` 정보 검색 품질을 향상시키는 방법`을 제공합니다. 사용자 쿼리와 유사한 추가 질문을 생성하고 OpenAI의 고급 언어 모델을 활용하여, 후속 작업에서 더 나은 이해와 더 정확한 응답을 제공할 가능성이 큽니다.

## API 사용에 대한 주의 사항

이 구현은 OpenAI의 API를 사용하므로 사용량에 따라 비용이 발생할 수 있습니다. OpenAI 계정 설정에서 사용량을 모니터링하고 적절한 한도를 설정하는 것이 좋습니다.


### Import libraries and set constants

In [3]:
import sys
import os
import re
from langchain.docstore.document import Document
from langchain.vectorstores import FAISS
from enum import Enum
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain_openai import ChatOpenAI
from typing import Any, Dict, List, Tuple

from dotenv import load_dotenv

load_dotenv()

os.environ["OPENAI_API_KEY"] = os.getenv('OPENAI_API_KEY')


sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..'))) # Add the parent directory to the path sicnce we work with notebooks

from helper_functions import *


class QuestionGeneration(Enum):
    """
        DOCUMENT_LEVEL: 문서 전체를 기준으로 질문 생성.
        FRAGMENT_LEVEL: 문서를 작은 조각으로 나누고 각 조각에 대해 질문 생성.
    """
    DOCUMENT_LEVEL = 1
    FRAGMENT_LEVEL = 2

# 문서를 나눌 때 최대 4000토큰, 중복 100토큰 
DOCUMENT_MAX_TOKENS = 4000
DOCUMENT_OVERLAP_TOKENS = 100

# 짧은 문서= 조각수준에서 나눌 때 128 토큰, 중복 16토큰으로 나눔 
FRAGMENT_MAX_TOKENS = 128
FRAGMENT_OVERLAP_TOKENS = 16

QUESTION_GENERATION = QuestionGeneration.DOCUMENT_LEVEL

# 문서나 조각 당 생성할 질문의 개수 
QUESTIONS_PER_DOCUMENT = 40

### Define classes and functions used by this pipeline

In [4]:
# 질문 목록 만드는 리스트 
class QuestionList(BaseModel):
    """
    문서 또는 조각에 대해 생성된 질문 목록을 나타내는 데이터 모델 클래스입니다.

    속성:
        question_list (List[str]): 문서 또는 조각을 위해 생성된 질문 목록
    """
    question_list: List[str] = Field(..., title="List of questions generated for the document or fragment")


# 쿼리 임베딩하는 클래스 
class OpenAIEmbeddingsWrapper(OpenAIEmbeddings):
    def __call__(self, query: str) -> List[float]:
        """
        인스턴스를 호출 가능한 객체로 만들어, 쿼리에 대한 임베딩을 생성할 수 있게 합니다.

        인자:
            query (str): 임베딩을 생성할 쿼리 문자열

        반환값:
            List[float]: 쿼리에 대한 임베딩을 실수 리스트 형식으로 반환
        """
        return self.embed_query(query)

    # 물음표롤 끝나는 문장만 리스트에 추가하여 내보내기 
def clean_and_filter_questions(questions: List[str]) -> List[str]:
    """
    질문 목록을 정리하고 필터링합니다.

    인자:
        questions (List[str]): 정리 및 필터링할 질문 목록

    반환값:
        List[str]: 정리 및 필터링된 질문 목록으로, 물음표로 끝나는 질문만 포함
    """
    cleaned_questions = []
    for question in questions:
        # 질문 앞에 붙은 숫자 제거 및 공백 정리
        cleaned_question = re.sub(r'^\d+\.\s*', '', question.strip())
        # 물음표로 끝나는 질문만 추가
        if cleaned_question.endswith('?'):
            cleaned_questions.append(cleaned_question)
    return cleaned_questions


# llm을 활용하여 문서가 주어졌을 때 질문을 추출하는 함수 
def generate_questions(text: str) -> List[str]:
    """
    제공된 텍스트를 기반으로 OpenAI 모델을 사용해 질문 목록을 생성합니다.

    인자:
        text (str): 질문을 생성할 컨텍스트 데이터

    반환값:
        List[str]: 중복되지 않고 필터링된 질문 목록
    """
    llm = ChatOpenAI(model="gpt-4o-mini", temperature=0)
    prompt = PromptTemplate(
        input_variables=["context", "num_questions"],
        template="Using the context data: {context}\n\nGenerate a list of at least {num_questions} "
                 "possible questions that can be asked about this context. Ensure the questions are "
                 "directly answerable within the context and do not include any answers or headers. "
                 "Separate the questions with a new line character."
    )
    chain = prompt | llm.with_structured_output(QuestionList)
    input_data = {"context": text, "num_questions": QUESTIONS_PER_DOCUMENT}
    result = chain.invoke(input_data)
    
    # QuestionList 객체에서 질문 목록 추출
    questions = result.question_list
    
    # 필터링하여 정리된 질문 목록 반환
    filtered_questions = clean_and_filter_questions(questions)
    return list(set(filtered_questions))

# 문서들을 활용하여 질문에 알맞는 답변을 생성하는 llm 
def generate_answer(content: str, question: str) -> str:
    """
    제공된 컨텍스트를 기반으로 특정 질문에 대한 답변을 생성합니다.

    인자:
        content (str): 답변을 생성하는 데 사용될 컨텍스트 데이터
        question (str): 답변을 생성할 질문

    반환값:
        str: 제공된 컨텍스트를 기반으로 한 간결하고 정확한 답변
    """
    llm = ChatOpenAI(model="gpt-4o-mini", temperature=0)
    prompt = PromptTemplate(
        input_variables=["context", "question"],
        template="Using the context data: {context}\n\nProvide a brief and precise answer to the question: {question}"
    )
    chain = prompt | llm
    input_data = {"context": content, "question": question}
    return chain.invoke(input_data)

# 문서를 더 작은 청크로 분할하는 함수 중복허용 
def split_document(document: str, chunk_size: int, chunk_overlap: int) -> List[str]:
    """
    문서를 더 작은 텍스트 청크로 분할합니다.

    인자:
        document (str): 분할할 문서의 텍스트
        chunk_size (int): 각 청크의 토큰 수 크기
        chunk_overlap (int): 연속된 청크 사이의 중첩되는 토큰 수

    반환값:
        List[str]: 각 청크가 문서 내용의 문자열인 텍스트 청크 목록
    """
    tokens = re.findall(r'\b\w+\b', document)  # 문서를 단어 토큰으로 분할
    chunks = []
    for i in range(0, len(tokens), chunk_size - chunk_overlap):
        chunk_tokens = tokens[i:i + chunk_size]
        chunks.append(chunk_tokens)
        if i + chunk_size >= len(tokens):  # 마지막 청크에 도달하면 반복 종료
            break
    return [" ".join(chunk) for chunk in chunks]  # 토큰 목록을 문자열로 변환하여 청크 목록 반환

# 주석과 함께 문서 내용 출력
def print_document(comment: str, document: Any) -> None:
    """
    주석과 함께 문서 내용을 출력합니다.

    인자:
        comment (str): 문서 세부 정보를 출력하기 전의 설명 또는 주석
        document (Any): 내용을 출력할 문서

    반환값:
        None
    """
    print(f'{comment} (type: {document.metadata["type"]}, index: {document.metadata["index"]}): {document.page_content}')

### Example usage


In [5]:
# Initialize OpenAIEmbeddings
embeddings = OpenAIEmbeddingsWrapper()

# Example document
example_text = "This is an example document. It contains information about various topics."

# 문서 기반 질문 생성 
questions = generate_questions(example_text)
print("Generated Questions:")
for q in questions:
    print(f"- {q}")

# 질문 기반 답변 생성 
sample_question = questions[0] if questions else "What is this document about?"
answer = generate_answer(example_text, sample_question)
print(f"\nQuestion: {sample_question}")
print(f"Answer: {answer}")

# 문서를 더 잘게 나누기 
chunks = split_document(example_text, chunk_size=10, chunk_overlap=2)
print("\nDocument Chunks:")
for i, chunk in enumerate(chunks):
    print(f"Chunk {i + 1}: {chunk}")

# 예시 문서를 임베딩함 
doc_embedding = embeddings.embed_documents([example_text])
# 쿼리를 임베딩함 
query_embedding = embeddings.embed_query("What is the main topic?")
print("\nDocument Embedding (first 5 elements):", doc_embedding[0][:5])
print("Query Embedding (first 5 elements):", query_embedding[:5])

Generated Questions:
- Are there any references or citations in the document?
- What is the main focus of the document?
- What are the key takeaways from the document?
- Does the document provide detailed information on each topic?
- Can the information in the document be applied in real-life situations?
- What is the publication date of the document?
- Is there a glossary of terms in the document?
- Is there a bibliography included in the document?
- Is the document part of a larger series?
- What type of information does the document contain?
- Is the document an example or a guide?
- Is the document accessible online?
- Can the document be used for educational purposes?
- Does the document include any visual aids?
- What is the significance of the topics discussed in the document?
- How many topics are covered in the document?
- Does the document provide any recommendations?
- Does the document include any charts or graphs?
- Does the document address any controversies?
- Is the doc

### Main pipeline
- 문서를 받았을 때 이를 조각으로 나누고 질문 생성한 후 벡터 스토어를 생성하여 검색기를 반환하는 함수 
1. 문서 전체를 중복 가능한 문서 조각으로 분할 
2. 해당 문서 조각을 더 작은 text_fragements로 분할 
3. 해당 조각을 documents 리스트에 저장 
4. 조각 수준에서 질문 생성 
5. 문서 조각 수준에서 질문 생성 
- 모든 

In [20]:
def process_documents(content: str, embedding_model: OpenAIEmbeddings):

    # 문서 전체 텍스트를 'text_documents'라는 중첩된 텍스트 조각으로 분할
    text_documents = split_document(content, DOCUMENT_MAX_TOKENS, DOCUMENT_OVERLAP_TOKENS)
    print(f'Text content split into: {len(text_documents)} documents')  # 분할된 문서 수 출력

    documents = []  # 최종 문서 조각을 저장할 리스트
    counter = 0  # 각 문서 조각의 인덱스
    for i, text_document in enumerate(text_documents):
        # 각 'text_document'를 더 작은 'text_fragments'로 다시 분할
        text_fragments = split_document(text_document, FRAGMENT_MAX_TOKENS, FRAGMENT_OVERLAP_TOKENS)
        print(f'Text document {i} - split into: {len(text_fragments)} fragments')  # 각 문서가 분할된 조각 수 출력
        
        for j, text_fragment in enumerate(text_fragments):
            # ORIGINAL 유형의 문서 조각을 documents에 추가
            documents.append(Document(
                page_content=text_fragment,  # 텍스트 조각 내용
                metadata={"type": "ORIGINAL", "index": counter, "text": text_document}  # 메타데이터 추가
            ))
            counter += 1
            
            # 'FRAGMENT_LEVEL'에서 질문 생성
            if QUESTION_GENERATION == QuestionGeneration.FRAGMENT_LEVEL:
                questions = generate_questions(text_fragment)  # 조각 수준에서 질문 생성
                documents.extend([
                    Document(page_content=question, metadata={"type": "AUGMENTED", "index": counter + idx, "text": text_document})
                    for idx, question in enumerate(questions)  # 각 질문에 대해 AUGMENTED 문서 조각 추가
                ])
                counter += len(questions)
                print(f'Text document {i} Text fragment {j} - generated: {len(questions)} questions')  # 생성된 질문 수 출력
        
        # 'DOCUMENT_LEVEL'에서 질문 생성
        if QUESTION_GENERATION == QuestionGeneration.DOCUMENT_LEVEL:
            questions = generate_questions(text_document)  # 문서 수준에서 질문 생성
            documents.extend([
                Document(page_content=question, metadata={"type": "AUGMENTED", "index": counter + idx, "text": text_document})
                for idx, question in enumerate(questions)  # 각 질문에 대해 AUGMENTED 문서 조각 추가
            ])
            counter += len(questions)
            print(f'Text document {i} - generated: {len(questions)} questions')  # 생성된 질문 수 출력

    # 모든 문서 조각 출력
    for document in documents:
        print_document("Dataset", document)

    print(f'Creating store, calculating embeddings for {len(documents)} FAISS documents')  # 벡터 스토어 생성 및 임베딩 계산 시작
    vectorstore = FAISS.from_documents(documents, embedding_model)  # FAISS 벡터 스토어 생성

    print("Creating retriever returning the most relevant FAISS document")
    return vectorstore.as_retriever(search_kwargs={"k": 1}), documents  # 가장 관련성 높은 문서 하나를 반환하도록 검색기 설정


### Example

In [25]:
document_query_retriever[1]

[Document(metadata={'type': 'ORIGINAL', 'index': 0, 'text': 'Understanding Climate Change Chapter 1 Introduction to Climate Change Climate change refers to significant long term changes in the global climate The term global climate encompasses the planet s overall weather patterns including temperature precipitation and wind patterns over an extended period Over the past century human activities particularly the burning of fossil fuels and deforestation have significantly contributed to climate change Historical Context The Earth s climate has changed throughout history Over the past 650 000 years there have been seven cycles of glacial advance and retreat with the abrupt end of the last ice age about 11 700 years ago marking the beginning of the modern climate era and human civilization Most of these climate changes are attributed to very small variations in Earth s orbit that change the amount of solar energy our planet receives During the Holocene epoch which began at the end of the

In [22]:

# Load sample PDF document to string variable
path = "../data/Understanding_Climate_Change.pdf"
content = read_pdf_to_string(path)

# Instantiate OpenAI Embeddings class that will be used by FAISS
embedding_model = OpenAIEmbeddings()

# Process documents and create retriever
document_query_retriever = process_documents(content, embedding_model)

Text content split into: 3 documents
Text document 0 - split into: 36 fragments
Text document 0 - generated: 46 questions
Text document 1 - split into: 36 fragments
Text document 1 - generated: 46 questions
Text document 2 - split into: 15 fragments
Text document 2 - generated: 43 questions
Dataset (type: ORIGINAL, index: 0): Understanding Climate Change Chapter 1 Introduction to Climate Change Climate change refers to significant long term changes in the global climate The term global climate encompasses the planet s overall weather patterns including temperature precipitation and wind patterns over an extended period Over the past century human activities particularly the burning of fossil fuels and deforestation have significantly contributed to climate change Historical Context The Earth s climate has changed throughout history Over the past 650 000 years there have been seven cycles of glacial advance and retreat with the abrupt end of the last ice age about 11 700 years ago marki

AttributeError: 'tuple' object has no attribute 'invoke'

In [27]:

# Example usage of the retriever
query = "What is climate change?"
retrieved_docs = document_query_retriever[0].invoke(query)
print(f"\nQuery: {query}")
print(f"Retrieved document: {retrieved_docs[0].page_content}")


Query: What is climate change?
Retrieved document: What is climate change?


In [29]:
retrieved_docs[0].metadata
# 증강된 문서가 뽑힘 

{'type': 'AUGMENTED',
 'index': 55,
 'text': 'Understanding Climate Change Chapter 1 Introduction to Climate Change Climate change refers to significant long term changes in the global climate The term global climate encompasses the planet s overall weather patterns including temperature precipitation and wind patterns over an extended period Over the past century human activities particularly the burning of fossil fuels and deforestation have significantly contributed to climate change Historical Context The Earth s climate has changed throughout history Over the past 650 000 years there have been seven cycles of glacial advance and retreat with the abrupt end of the last ice age about 11 700 years ago marking the beginning of the modern climate era and human civilization Most of these climate changes are attributed to very small variations in Earth s orbit that change the amount of solar energy our planet receives During the Holocene epoch which began at the end of the last ice age h

### FAISS에서 가장 관려높은 문서를 뽑을 때 오리지널보다 증강된 질문에 대한 문서가 뽑힐 확률이  높다. 

In [30]:
query = "How do freshwater ecosystems change due to alterations in climatic factors?"
print (f'Question:{os.linesep}{query}{os.linesep}')
retrieved_documents = document_query_retriever[0].invoke(query)

for doc in retrieved_documents:
    print_document("Relevant fragment retrieved", doc)

Question:
How do freshwater ecosystems change due to alterations in climatic factors?

Relevant fragment retrieved (type: AUGMENTED, index: 69): How are freshwater ecosystems being affected by climate change?


### Find the parent text document and use it as context for the generative model to generate an answer to the question.

In [31]:
context = doc.metadata['text']
print (f'{os.linesep}Context:{os.linesep}{context}')
answer = generate_answer(context, query)
print(f'{os.linesep}Answer:{os.linesep}{answer}')


Context:
Understanding Climate Change Chapter 1 Introduction to Climate Change Climate change refers to significant long term changes in the global climate The term global climate encompasses the planet s overall weather patterns including temperature precipitation and wind patterns over an extended period Over the past century human activities particularly the burning of fossil fuels and deforestation have significantly contributed to climate change Historical Context The Earth s climate has changed throughout history Over the past 650 000 years there have been seven cycles of glacial advance and retreat with the abrupt end of the last ice age about 11 700 years ago marking the beginning of the modern climate era and human civilization Most of these climate changes are attributed to very small variations in Earth s orbit that change the amount of solar energy our planet receives During the Holocene epoch which began at the end of the last ice age human societies flourished but the in

### 내 생각 
- 문서를 넣고 문서를 문장 단위로, 조각 단위로 쪼갠 후에 각각 문서에 알맞는 질문을 생성함 
- 이를 벡터db로 넣은 다음에 질문을 했을 때 질문과 가장 유사한 질문에 해당되는 문서를 뽑는 방식 
- 문서로 질문을 만들고 , 질문으로 유사한 질문을 뽑아 , 질문에 해당되는 문서를 반환함으로써 질문으로 바로 문서를 뽑을 때보다 더 정확한 답변을 얻을 수 있다. 